In [2]:
import pandas as pd
import geopandas as gpd
import numpy as np

In [3]:
maize_hist = pd.read_csv('./Gridcell_summary_maize_1990_2019_historical_SSP370_IPSL-CM6A-LR.csv')
maize_126 = pd.read_csv('./Gridcell_summary_maize_2035_2064_future_SSP126_IPSL-CM6A-LR.csv')
maize_370 = pd.read_csv('./Gridcell_summary_maize_2035_2064_future_SSP370_IPSL-CM6A-LR.csv')

In [6]:
# return the minimum  value of maize_hist["sowingYear"] and maize_126["sowingYear"]
min(maize_hist["SowingYear"].min(), maize_126["SowingYear"].max(), maize_370["SowingYear"].max())


1990

In [14]:
maize_hist

Exp. Species.  Trt.  row  col   long    lat  SowingDate  Duration   
0        76692    maize    77  107  372   5.75  36.75  1996-03-20       115  \
1        76692    maize    77  107  372   5.75  36.75  1995-03-21       120   
2        76692    maize    77  107  372   5.75  36.75  2010-03-21       116   
3        76692    maize    77  107  372   5.75  36.75  2004-03-20       120   
4        76692    maize    77  107  372   5.75  36.75  1991-03-21       114   
...        ...      ...   ...  ...  ...    ...    ...         ...       ...   
153526  179680    maize  5354  250  400  19.75 -34.75  1994-12-26        82   
153527  179680    maize  5354  250  400  19.75 -34.75  1996-12-25        76   
153528  179680    maize  5354  250  400  19.75 -34.75  1991-12-26        84   
153529  179680    maize  5354  250  400  19.75 -34.75  2006-12-26        80   
153530  179680    maize  5354  250  400  19.75 -34.75  2001-12-26        82   

        Biomass  Yield MaturityDay  SowingYear  MaturityYear  
0           238     81  1996-07-13        1996          1996  
1          5677   1930  1995-07-19        1995          1995  
2           594    202  2010-07-15        2010          2010  
3          2075    705  2004-07-18        2004          2004  
4           202     69  1991-07-13        1991          1991  
...         ...    ...         ...         ...           ...  
153526      146     50  1995-03-18        1994          1995  
153527       11      4  1997-03-11        1996          1997  
153528      233     79  1992-03-19        1991          1992  
153529       81     28  2007-03-16        2006          2007  
153530      554    188  2002-03-18        2001          2002  

[153531 rows x 14 columns]

In [5]:
maize_hist

Exp. Species.  Trt.  row  col   long    lat  SowingDate  Duration   
0        76692    maize    77  107  372   5.75  36.75  1996-03-20       115  \
1        76692    maize    77  107  372   5.75  36.75  1995-03-21       120   
2        76692    maize    77  107  372   5.75  36.75  2010-03-21       116   
3        76692    maize    77  107  372   5.75  36.75  2004-03-20       120   
4        76692    maize    77  107  372   5.75  36.75  1991-03-21       114   
...        ...      ...   ...  ...  ...    ...    ...         ...       ...   
153526  179680    maize  5354  250  400  19.75 -34.75  1994-12-26        82   
153527  179680    maize  5354  250  400  19.75 -34.75  1996-12-25        76   
153528  179680    maize  5354  250  400  19.75 -34.75  1991-12-26        84   
153529  179680    maize  5354  250  400  19.75 -34.75  2006-12-26        80   
153530  179680    maize  5354  250  400  19.75 -34.75  2001-12-26        82   

        Biomass  Yield MaturityDay  SowingYear  MaturityYear  
0           238     81  1996-07-13        1996          1996  
1          5677   1930  1995-07-19        1995          1995  
2           594    202  2010-07-15        2010          2010  
3          2075    705  2004-07-18        2004          2004  
4           202     69  1991-07-13        1991          1991  
...         ...    ...         ...         ...           ...  
153526      146     50  1995-03-18        1994          1995  
153527       11      4  1997-03-11        1996          1997  
153528      233     79  1992-03-19        1991          1992  
153529       81     28  2007-03-16        2006          2007  
153530      554    188  2002-03-18        2001          2002  

[153531 rows x 14 columns]

In [26]:
grid_gdf = gpd.read_file('./grid.geojson')

In [30]:
# create a dataframe that averages all the rows that share the same "Exp." values and only keeps lat, long, Yield, Biomass, and Duration columns
def average_rows(df, string, grid_df):
    working_df = df[["Exp.", "Yield", "Biomass", "Duration"]].groupby("Exp.").mean().reset_index()
    # add string to "Yield", "Biomass", "Duration" column names
    working_df = working_df.rename(columns={"Yield": "Yield" + string, "Biomass": "Biomass" + string, "Duration": "Duration" + string})
    # merge working_df with grid_df on "Exp." column
    working_df = pd.merge(grid_df, working_df, on="Exp.")
    return working_df

In [32]:
maize = average_rows(maize_hist, "_maize_hist", grid_gdf)
maize = average_rows(maize_126, "_maize_126", maize)
maize = average_rows(maize_370, "_maize_370", maize)

In [34]:
maize.columns = map(str.lower, maize.columns)

In [36]:
maize["yield_ratio_maize_126"] = maize["yield_maize_126"] / maize["yield_maize_hist"]
maize["yield_ratio_maize_370"] = maize["yield_maize_370"] / maize["yield_maize_hist"]

In [38]:
maize.explore()

In [39]:
# write maize to geojson file
maize.to_file("./maize_ratios.geojson", driver="GeoJSON")

In [50]:
# make a dictionary of the quantiles of ratios of the columns of maize, the format should be 0.01: {"yield_ratio_maize_126": 0.0, "yield_ratio_maize_370": 0.0, etc. and include 0.01, 0.02, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 0.98, 0.99
maize_quantiles = {}
col_list = ["yield_ratio_maize_126", "yield_ratio_maize_370", "yield_maize_hist", "yield_maize_126", "yield_maize_370", "biomass_maize_hist", "biomass_maize_126", "biomass_maize_370", "duration_maize_hist", "duration_maize_126", "duration_maize_370"]
q_list = ["min", 0.01, 0.02, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 0.98, 0.99, "max"]




for col in col_list:
    quantile_dict = {}  # Create a dictionary for the current column
    for quantile in q_list:
        if quantile == "min":
            quantile_value = maize[col].min()
            quantile_dict[quantile] = quantile_value

        elif quantile == "max":
            quantile_value = maize[col].max()
            quantile_dict[quantile] = quantile_value
        else:
            quantile_value = maize[col].quantile(quantile)  # Calculate the quantile value
            quantile_dict[f"quantile_{int(quantile * 100)}"] = quantile_value  # Add to the dictionary
    maize_quantiles[col] = quantile_dict  # Add the quantile dictionary to the main dictionary

maize_quantiles


{'yield_ratio_maize_126': {'min': 0.0,
  0.01: 0.320679826244946,
  0.02: 0.3665178117368092,
  0.1: 0.5078634642928715,
  0.2: 0.603901278295438,
  0.3: 0.6812192339734442,
  0.4: 0.7511014446979176,
  0.5: 0.8222431308226588,
  0.6: 0.8856544020092065,
  0.7: 0.9462014907604208,
  0.8: 0.9907185066550891,
  0.9: 1.0578471081092335,
  0.98: 1.3141182515987966,
  0.99: 1.4587238067925545,
  'max': inf},
 'yield_ratio_maize_370': {'min': 0.0,
  0.01: 0.21719770363899676,
  0.02: 0.2519661786087626,
  0.1: 0.3729102970189739,
  0.2: 0.46544588894156774,
  0.3: 0.5564343901788148,
  0.4: 0.6513872530893962,
  0.5: 0.7538395104184578,
  0.6: 0.8408960864918201,
  0.7: 0.9193339085360102,
  0.8: 0.9802138984990384,
  0.9: 1.1022211800742965,
  0.98: 1.5536560160306123,
  0.99: 1.8411379005300281,
  'max': 5.5528455284552845},
 'yield_maize_hist': {'min': 0.0,
  0.01: 6.199333333333334,
  0.02: 11.264666666666669,
  0.1: 230.8,
  0.2: 800.1533333333332,
  0.3: 1486.8296296296296,
  0.4: 2200